### Pump it Up: Data Mining the Water Table

In [1]:
import sys

sys.path.append("../")

In [2]:
from datetime import datetime

import seaborn as sns
from numpy import NaN
from pandas import DataFrame, Series, read_csv, to_datetime
from pandas_profiling import ProfileReport
from utils import (
    cumulatively_categorise_number,
    display_all,
    dummies,
    extract_date_features,
    fix_construction_year,
    fix_funder_installer,
    fix_locations,
    season_mapper,
)

### Load the training set features and labels

#### Load the training data

In [3]:
df_train_feat = read_csv("../data/training_set_features.csv")
df_train_feat.shape

(59400, 40)

In [4]:
df_train_labels = read_csv("../data/training_set_labels.csv")
df_train_labels.shape

(59400, 2)

#### Load the test data

In [5]:
df_test_feat = read_csv("../data/test_set_values.csv")
df_test_feat.shape

(14850, 40)

## Inspecting and cleaning the data

In [41]:
# ProfileReport generates a nice overview of the distributions in the variables
# as well as warnings about the cardinality of variables and correlation between variables
ProfileReport(df_train_feat)

Summarize dataset:   0%|          | 0/38 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### 1. Highly correlated columns

The ProfileReport warns about quite a few columns which are highly correlated.  
Therefore, we might be able to remove a few columns, without losing a lot of information.  
Also, it is in general desirable to remove features with high correlation.  
Removing columns in the first step, will make it easier to cope with column contents in a later step (as there will be fewer columns to deal with).

##### extraction_type, extraction_type_group and extraction_type_class
The output of the cell below confirms that extraction_type and extraction_type_group are very similar in terms of values.
They seem to represent almost the same information at a very similar level of granularity, where extraction_type is slightly more granular than extraction_type_group (they both contain some brand information). 

In [7]:
df_train_feat.groupby(
    ["extraction_type_class", "extraction_type_group", "extraction_type"]
).size().reset_index().rename(columns={0: "count"})

extraction_type_class extraction_type_group            extraction_type  \
0                gravity               gravity                    gravity   
1               handpump               afridev                    afridev   
2               handpump         india mark ii              india mark ii   
3               handpump        india mark iii             india mark iii   
4               handpump           nira/tanira                nira/tanira   
5               handpump        other handpump  other - mkulima/shinyanga   
6               handpump        other handpump          other - play pump   
7               handpump        other handpump             other - swn 81   
8               handpump        other handpump                     walimi   
9               handpump                swn 80                     swn 80   
10             motorpump                  mono                       mono   
11             motorpump       other motorpump                       cemo   
12             motorpump       other motorpump                     climax   
13                 other                 other                      other   
14             rope pump             rope pump          other - rope pump   
15           submersible           submersible                        ksb   
16           submersible           submersible                submersible   
17          wind-powered          wind-powered                   windmill   

    count  
0   26780  
1    1770  
2    2400  
3      98  
4    8154  
5       2  
6      85  
7     229  
8      48  
9    3670  
10   2865  
11     90  
12     32  
13   6430  
14    451  
15   1415  
16   4764  
17    117

I choose to retain extraction_type_class and drop the other 2 related columns.  
Thus, I choose for low cardinality, while losing some level of detail (the brand information).

In [8]:
drop_cols = {"extraction_type_group", "extraction_type"}

##### payment and payment_type
payment and payment type represent the exact same information, just formulated differently.  
The choice of column is therefore arbitrary. I choose to drop the payment column.

In [9]:
# payment and payment type represent the exact same information, just formulated differently
df_train_feat.groupby(["payment", "payment_type"]).size().reset_index().rename(
    columns={0: "count"}
)

payment payment_type  count
0              never pay    never pay  25348
1                  other        other   1054
2           pay annually     annually   3642
3            pay monthly      monthly   8300
4         pay per bucket   per bucket   8985
5  pay when scheme fails   on failure   3914
6                unknown      unknown   8157

In [10]:
drop_cols.update({"payment"})

##### management and management_group
management is more granular than management group.  
I choose to drop management group and keep the more granular management column.  
Also, the valuus 'trust', 'other - school', and 'unknown' are all changed to 'other'.

In [11]:
df_train_feat.groupby(["management_group", "management"]).size().reset_index().rename(
    columns={0: "count"}
)

management_group        management  count
0        commercial           company    685
1        commercial  private operator   1971
2        commercial             trust     78
3        commercial   water authority    904
4             other             other    844
5             other    other - school     99
6        parastatal        parastatal   1768
7           unknown           unknown    561
8        user-group               vwc  40507
9        user-group       water board   2933
10       user-group               wua   2535
11       user-group               wug   6515

In [12]:
df_train_feat.loc[
    df_train_feat["management"].isin(["trust", "other - school", "unknown"]),
    "management",
] = "other"
df_test_feat.loc[
    df_test_feat["management"].isin(["trust", "other - school", "unknown"]),
    "management",
] = "other"

In [13]:
drop_cols.update({"management"})

##### quality_group and water_quality
water_quality offers a bit more detail than quality_group, but it results in values with lower occurence (fluoride abondonded).  
I choose to remove water_quality and keep quality_group.

In [14]:
df_train_feat.groupby(["quality_group", "water_quality"]).size().reset_index().rename(
    columns={0: "count"}
)

quality_group       water_quality  count
0       colored            coloured    490
1      fluoride            fluoride    200
2      fluoride  fluoride abandoned     17
3          good                soft  50818
4         milky               milky    804
5         salty               salty   4856
6         salty     salty abandoned    339
7       unknown             unknown   1876

In [15]:
drop_cols.update({"water_quality"})

##### quantity and quantity_group
quantity and quantity_group represent the exact same information, just formulated differently.  
The choice of column is therefore arbitrary. I choose to drop the quantity_group column.

In [16]:
df_train_feat.groupby(["quantity_group", "quantity"]).size().reset_index().rename(
    columns={0: "count"}
)

quantity_group      quantity  count
0            dry           dry   6246
1         enough        enough  33186
2   insufficient  insufficient  15129
3       seasonal      seasonal   4050
4        unknown       unknown    789

In [17]:
drop_cols.update({"quantity_group"})

##### source, source_type and source_class

In [18]:
df_train_feat.groupby(
    ["source_class", "source_type", "source"]
).size().reset_index().rename(columns={0: "count"})

source_class           source_type                source  count
0  groundwater              borehole              hand dtw    874
1  groundwater              borehole           machine dbh  11075
2  groundwater          shallow well          shallow well  16824
3  groundwater                spring                spring  17021
4      surface                   dam                   dam    656
5      surface  rainwater harvesting  rainwater harvesting   2295
6      surface            river/lake                  lake    765
7      surface            river/lake                 river   9612
8      unknown                 other                 other    212
9      unknown                 other               unknown     66

In [19]:
drop_cols.update({"source_class", "source"})

##### waterpoint_type and waterpoint_type_group

waterpoint_type and waterpoint_type_group represent the exact same information, just formulated differently.  
The choice of column is therefore arbitrary. I choose to drop the waterpoint_type_group column.  
I also change the 7 'dam' values to other.  

In [20]:
df_train_feat.groupby(
    ["waterpoint_type", "waterpoint_type_group"]
).size().reset_index().rename(columns={0: "count"})

waterpoint_type waterpoint_type_group  count
0                cattle trough         cattle trough    116
1           communal standpipe    communal standpipe  28522
2  communal standpipe multiple    communal standpipe   6103
3                          dam                   dam      7
4                    hand pump             hand pump  17488
5              improved spring       improved spring    784
6                        other                 other   6380

In [21]:
df_train_feat.loc[
    df_train_feat["waterpoint_type"].isin(["dam"]), "waterpoint_type"
] = "other"
df_test_feat.loc[
    df_test_feat["waterpoint_type"].isin(["dam"]), "waterpoint_type"
] = "other"

In [22]:
drop_cols.update({"waterpoint_type_group"})

In [23]:
drop_cols

{'extraction_type',
 'extraction_type_group',
 'management',
 'payment',
 'quantity_group',
 'source',
 'source_class',
 'water_quality',
 'waterpoint_type_group'}

### 2. useless columns
upon further inspection, some columns seem useless and will be dropped.
- id: can be assumed to be a random number, so it should be dropped for prediction **(it is kept for now, to join features and labels later on)**.
- amount_tsh has a lot of '0' values, even for functional pumps. It is hard to imagine that this is real data, so I choose to drop this column.
- num_private has 58643 (98.7%) zeros in the training set. There is also no information on the meaning of the column on the website.
- scheme_name has 47.4% missing values in the training set.
- recorded_by: constant value --> useless feature
- wpt_name: the name of the waterpoint. Seems useless and has very high cardinality --> good riddance.
- region_code: one would assume that there is one region_code per region, but this is not the case. Due to its stange nature, region_code is dropped.

In [24]:
drop_cols.update(
    {
        "amount_tsh",
        "num_private",
        "scheme_name",
        "recorded_by",
        "wpt_name",
        "region_code",
    }
)

In [25]:
df_train_feat = df_train_feat.drop(columns=drop_cols)
df_test_feat = df_test_feat.drop(columns=drop_cols)

### 3. Dealing with missing values
Missing values could be represented by 'NA' values, but they might also be hidden.
For instance, in numerical columns, **0** values could actually point to misisng values

In [26]:
na_counts_train = df_train_feat.isna().sum()
cols_with_na_vals_train = list(na_counts_train[na_counts_train > 0].index)
cols_with_na_vals_train

['funder',
 'installer',
 'subvillage',
 'public_meeting',
 'scheme_management',
 'permit']

In [27]:
na_counts_test = df_test_feat.isna().sum()
cols_with_na_vals_test = list(na_counts_test[na_counts_test > 0].index)
cols_with_na_vals_test

['funder',
 'installer',
 'subvillage',
 'public_meeting',
 'scheme_management',
 'permit']

As a quick solution, I choose to impute all NA values with the mode (none of the columns are numerical)

In [28]:
df_train_feat[cols_with_na_vals_train] = df_train_feat[cols_with_na_vals_train].fillna(
    df_train_feat.mode().iloc[0]
)
df_test_feat[cols_with_na_vals_test] = df_test_feat[cols_with_na_vals_test].fillna(
    df_test_feat.mode().iloc[0]
)

#### longitude, latitude, gps_height, population
Zero values in these columns are suspicious.
- Longitude values of 0 are not possible in Tanzania.
- Latitude values of 0 occur only for Shinyanga and Mwanza. A quick look at Google maps shows that these regions have latitude values that are quite different from 0
- gps_height could technically be 0 for some records, but not 34.4%, as is the case for the training set. Theoretically, it would be possible to look up the exact gps height for a certain latitude and longitude. However, I did not find a decently quick way to do this for many points.
- population is unlikely to be 0.

In [29]:
# impute the longitude, latitude, gps_height and population
df_train_feat, df_test_feat = fix_locations(df_train_feat, df_test_feat)

### 4. Dealing with high-cardinality data
The ProfileReport warns about **6** variables with high cardinality in the data.  
Depending on the contents of the data, the meaning of the data and the exact cardinality, we can deal with these data in different ways.

##### date_recorded

In [30]:
df_train_feat, df_test_feat = fix_construction_year(df_train_feat, df_test_feat)

In [31]:
# Extract some additional data features: from the date_recorded column (month_recorded, year_recorded, season_recorded)
df_train_feat = extract_date_features(df_train_feat, fieldname_date="date_recorded")
df_test_feat = extract_date_features(df_test_feat, fieldname_date="date_recorded")

##### Installer & Funder
Both installer and funder have very high cardinality (2145, 1897 respectively).  
However, there are some intuitive relations between these columns and the status of the pumps.  
It is reasonable to assume, for instance, that pumps funded by the government are maintained differntly than those owned funded by private instances.  
As I only had limited time to take on this case, I had no time to study the individual values. 
Instead, I choose to retain the top 10 categories (in terms of value counts) for installer and funder.

In [32]:
# impute the installer & funder
df_train_feat, df_test_feat = fix_funder_installer(df_train_feat, df_test_feat)

In [33]:
# training set
(
    df_train_feat.loc[:, "installer"],
    installer_categories,
) = cumulatively_categorise_number(
    column=df_train_feat["installer"], return_categories_list=True
)
df_train_feat.loc[:, "funder"], funder_categories = cumulatively_categorise_number(
    column=df_train_feat["funder"], return_categories_list=True
)
# df_train_feat.drop(columns = {"installer", "funder"}, inplace = True)

In [35]:
# test set (the bins should match those in the training set)
df_test_feat["installer"] = df_test_feat["installer"].apply(
    lambda x: x if x in installer_categories else "Other"
)
df_test_feat["funder"] = df_test_feat["funder"].apply(
    lambda x: x if x in funder_categories else "Other"
)

### 5. Drop columns that are no longer needed and write the dataframes to csv files.

In [36]:
df_train_feat.drop(
    columns=["subvillage", "lga", "ward", "construction_year"], inplace=True
)
df_test_feat.drop(
    columns=["subvillage", "lga", "ward", "construction_year"], inplace=True
)

In [37]:
df_train_feat.to_csv("../data/train_features_cleaned_businessplan.csv", index=False)

In [38]:
df_train_clean, df_test_clean = dummies(df_train_feat, df_test_feat)

In [39]:
df_train_clean.to_csv("../data/train_features_cleaned.csv", index=False)

In [40]:
df_test_clean.to_csv("../data/test_features_cleaned.csv", index=False)